In [31]:
import igraph
import snap
import math
import numpy as np
from lasso import lasso
from numpy.random import default_rng

rng = default_rng()

graph = snap.LoadEdgeList(snap.TNGraph, "p2p-Gnutella08.txt", 0, 1)

print("Nodes and Edges: (",graph.GetNodes(), graph.GetEdges(),")")

n = graph.GetNodes()

k = 1  # Parameter
k1 = 2*k

epsilon = 0.15  # \in (0,1/6)
theta = 0.1  # \in [0,1)
mu = 1  # >0
C = 2  # >1

d = (1/epsilon) * (np.log(np.e * (theta+1) * n)/np.log(mu * C))
m = (1/epsilon) * C * d * k1

d = math.ceil(d)
m = math.ceil(m)
print("d: ",d)
print("m: ",m)

scoreMat = np.zeros((n, 1))
A = np.zeros((m, n))

for j in range(n):  # 0 ... n-1
    # Select d numbers without replacement from 0 ... m-1
    row = rng.choice(m, size=d, replace=False)
    A[row, j] = 1
# Measurement matrix constructed


for u in graph.Nodes():
    v = u.GetId()
    num_nbrs, nbrs = graph.GetNodesAtHop(v, 1, False)
    nbrs.insert(0, v)
    egoadj = np.zeros((len(nbrs), len(nbrs)))
    for i, v1 in enumerate(nbrs):
        for j, v2 in enumerate(nbrs):
            if v1 != v2:
                egoadj[i, j] = 1 if graph.IsEdge(
                    v1, v2) else 0
    adj2 = np.dot(egoadj, egoadj)
    score = 0
    for (x, y), value in np.ndenumerate(egoadj):
        # 1-egoAdj comes from the value==0 condition
        if x < y and value == 0 and adj2[x, y] != 0:
            score = score + 1 / (adj2[x, y])
    scoreMat[v] = score

scoreMat = scoreMat/np.linalg.norm(scoreMat)  # Normalize the scores

y = np.zeros((m, 1))  # This is the matrix we get as measured in real life
for i in range(m):
    y[i] = A[i, :].dot(scoreMat)

print("True Local Betweenness Values: ")
print(scoreMat)
print()
x = lasso(A, y)

print("Reconstructed Local Betweenness Values: ")
print(x)

MSE = np.linalg.norm(scoreMat-x)
print("Relative L2-Norm Error Percentage: ", 100*MSE, "%")
# print(np.linalg.norm(scoreMat)) # This is ofc 1

Nodes and Edges: ( 6301 20777 )
d:  95
m:  2525
True Local Betweenness Values: 
[[0.]
 [0.]
 [0.]
 ...
 [0.]
 [0.]
 [0.]]

2525 6301
Reconstructed Local Betweenness Values: 
[[ 8.55628529e-07]
 [ 1.06653319e-06]
 [-1.21924623e-07]
 ...
 [-6.18073580e-07]
 [ 3.36940723e-07]
 [ 5.24946142e-07]]
Relative L2-Norm Error Percentage:  0.008467957520604714 %


In [32]:
g = igraph.Graph([(e.GetSrcNId(), e.GetDstNId()) for e in graph.Edges()])
g.vs["loc_btwness"] = x.flatten()
layout = g.layout("kk")

In [34]:
topk=4 ## Change this to get the topK information flow hotspots
visual_style = {}
visual_style["vertex_size"] = [50*wt for wt in g.vs["loc_btwness"]]
visual_style["edge_width"] = 0.1
visual_style["layout"] = layout
visual_style["bbox"] = (500, 500)
visual_style["edge_color"] = "DodgerBlue"

idxTopK = np.argpartition(g.vs["loc_btwness"], -topk)[-topk:]  # Indices not sorted
print("Top ",topk," information flow hotspots: ", idxTopK)

visual_style["vertex_label"] = [node if node in idx else None for node, val in enumerate(g.vs["loc_btwness"])]
visual_style["vertex_label_dist"] = 0
visual_style["vertex_label_angle"] = 0.5
visual_style["vertex_label_size"] = 8
igraph.plot(g, **visual_style)

Top  4  information flow hotspots:  [143 249 147 367]
